In [1]:
import folium
import pandas as pd
import branca.colormap as cm
import json
import requests
import io
from shapely.geometry import shape
import ast
import warnings

# Suppress the specific warnings for a cleaner output
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
warnings.filterwarnings('ignore', category=FutureWarning)

# Load the CSV files
cost_df = pd.read_csv("data/CostOfLiving.csv")
gpi_df = pd.read_csv("data/GPI.csv")
temp_df = pd.read_csv("data/combined_temperature.csv")
restaurants_df = pd.read_csv("data/TA_restaurants_europa.csv")

# Clean column names and country names for cost_df
cost_df.columns = cost_df.columns.str.strip()
cost_df['Country'] = cost_df['Country'].str.strip()  # Remove leading/trailing spaces

# Process temperature data to get the most recent year for each country
temp_df_latest = temp_df.sort_values('Year').groupby('Country').last().reset_index()
temp_df_latest = temp_df_latest[['Country', 'Annual Mean', 'Code']]
temp_df_latest.columns = ['Country', 'Annual_Mean_Temperature', 'iso3c']

# Process GPI data to get the most recent year for each country
gpi_latest = gpi_df[['Country', 'iso3c', '2023']]
gpi_latest.columns = ['Country', 'iso3c', 'GPI']

# Get list of countries from cost of living data
cost_countries = cost_df['Country'].unique()

# Define country name mapping
country_name_map = {
    'United States': 'United States of America',
    'Russia': 'Russian Federation',
    'South Korea': 'Korea, Republic of',
    'Iran': 'Iran, Islamic Republic of',
    'Vietnam': 'Viet Nam',
    'Venezuela': 'Venezuela, Bolivarian Republic of',
    'Tanzania': 'Tanzania, United Republic of',
    'Syria': 'Syrian Arab Republic',
    'Moldova': 'Moldova, Republic of',
    'Taiwan': 'Taiwan, Province of China',
    'Bolivia': 'Bolivia, Plurinational State of',
    'Ivory Coast': "Côte d'Ivoire",
    'North Macedonia': 'Macedonia, the former Yugoslav Republic of',
    'Libya': 'Libyan Arab Jamahiriya',
    'Bosnia And Herzegovina': 'Bosnia and Herzegovina',
    'Brunei': 'Brunei Darussalam',
    'United Kingdom': 'United Kingdom',
    'Us Virgin Islands': 'Virgin Islands, U.S.',
    'Hong Kong (China)': 'Hong Kong',
    'Macao (China)': 'Macao',
    'China': 'China',
    'Kosovo (Disputed Territory)': 'Kosovo',
    'Trinidad And Tobago': 'Trinidad and Tobago',
    'United Arab Emirates': 'United Arab Emirates',
    'Dominican Republic': 'Dominican Republic',
    'Czech Republic': 'Czech Republic',
    'New Zealand': 'New Zealand',
    'Costa Rica': 'Costa Rica',
    'El Salvador': 'El Salvador',
    'Saudi Arabia': 'Saudi Arabia',
    'South Africa': 'South Africa',
    'Papua New Guinea': 'Papua New Guinea',
    'Netherlands': 'Netherlands',
    'United States of America': 'United States',
    'Bahamas,': 'Bahamas',
    'Congo, Dem. Rep.': 'Democratic Republic of the Congo',
    'Iran, Islamic Rep.': 'Iran',
    'Kyrgyz Republic': 'Kyrgyzstan',
    'Korea, Rep.': 'South Korea',
    'Russian Federation': 'Russia',
    'Slovak Republic': 'Slovakia',
    'Syrian Arab Republic': 'Syria',
    'Yemen, Rep.': 'Yemen',
    'Venezuela, Rb': 'Venezuela',
    'Turkiye': 'Turkey',
    'Bosnia and Herzegovina': 'Bosnia And Herzegovina',
    'Trinidad and Tobago': 'Trinidad And Tobago',
    'United Arab Emirates': 'United Arab Emirates'
}

# Create comprehensive mappings to standardize to Cost of Living format
temperature_to_cost_map = {
    'United States': 'United States',
    'United Arab Emirates': 'United Arab Emirates', 
    'United Kingdom': 'United Kingdom',
    'Russian Federation': 'Russia',
    'Bahamas,': 'Bahamas',
    'Korea, Rep.': 'South Korea',
    'Korea-': 'South Korea',
    'Iran, Islamic Rep.': 'Iran',
    'Syrian Arab Republic': 'Syria',
    'Yemen, Rep.': 'Yemen',
    'Venezuela, Rb': 'Venezuela',
    'Kyrgyz Republic': 'Kyrgyzstan',
    'Slovak Republic': 'Slovakia',
    'Congo, Dem. Rep.': 'Democratic Republic of the Congo',
    'Timor Leste': 'Timor-Leste',
    'Cote d\'Ivoire': 'Ivory Coast',
    'Gambia,': 'Gambia',
    'Trinidad And Tobago': 'Trinidad And Tobago',
    'Guinea Bissau': 'Guinea-Bissau',
    'Bosnia And Herzegovina': 'Bosnia And Herzegovina',
    'Dominican Republic': 'Dominican Republic',
    'Czech Republic': 'Czech Republic',
    'Costa Rica': 'Costa Rica',
    'El Salvador': 'El Salvador',
    'Saudi Arabia': 'Saudi Arabia',
    'South Africa': 'South Africa',
    'Papua New Guinea': 'Papua New Guinea',
    'New Zealand': 'New Zealand',
    'Turkey': 'Turkey'
}

gpi_to_cost_map = {
    'United States of America': 'United States',
    'Bosnia and Herzegovina': 'Bosnia And Herzegovina',
    'Trinidad and Tobago': 'Trinidad And Tobago', 
    'Cote d\' Ivoire': 'Ivory Coast',
    'Democratic Republic of the Congo': 'Democratic Republic of the Congo',
    'Republic of the Congo': 'Republic of the Congo',
    'Czech Republic': 'Czech Republic',
    'Dominican Republic': 'Dominican Republic',
    'El Salvador': 'El Salvador',
    'Saudi Arabia': 'Saudi Arabia',
    'South Africa': 'South Africa',
    'Costa Rica': 'Costa Rica',
    'Papua New Guinea': 'Papua New Guinea',
    'New Zealand': 'New Zealand',
    'United Arab Emirates': 'United Arab Emirates',
    'United Kingdom': 'United Kingdom',
    'The Gambia': 'Gambia',
    'Timor-Leste': 'Timor-Leste',
    'North Macedonia': 'North Macedonia',
    'South Korea': 'South Korea',
    'Kyrgyz Republic': 'Kyrgyzstan',
    'Turkiye': 'Turkey',
    'Guinea-Bissau': 'Guinea-Bissau'
}

# Standardize temperature data
temp_df_latest_mapped = temp_df_latest.copy()
for index, row in temp_df_latest_mapped.iterrows():
    country = row['Country'].strip()
    # Apply mapping if exists, otherwise keep original
    standardized_country = temperature_to_cost_map.get(country, country)
    temp_df_latest_mapped.at[index, 'Country'] = standardized_country

# Filter temperature data to keep only countries in cost of living
temp_df_latest = temp_df_latest_mapped[temp_df_latest_mapped['Country'].str.strip().isin(cost_countries)]

# Standardize GPI data
gpi_latest_mapped = gpi_latest.copy()
for index, row in gpi_latest_mapped.iterrows():
    country = row['Country'].strip()
    # Apply mapping if exists, otherwise keep original
    standardized_country = gpi_to_cost_map.get(country, country)
    gpi_latest_mapped.at[index, 'Country'] = standardized_country

# Filter GPI data to keep only countries in cost of living
gpi_latest = gpi_latest_mapped[gpi_latest_mapped['Country'].str.strip().isin(cost_countries)]
# Process restaurant data
# Convert cuisine styles string to list
restaurants_df['Cuisine Style'] = restaurants_df['Cuisine Style'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else [])

# Create a list where each cuisine is a separate row
cuisines_list = []
for idx, row in restaurants_df.iterrows():
    for cuisine in row['Cuisine Style']:
        cuisines_list.append({
            'city': row['City'],
            'place': row['Name'],
            'cuisine_style': cuisine,
            'rating': row['Rating'],
            'reviews_number': row['Number of Reviews']
        })

cuisines_list = pd.DataFrame(cuisines_list)

# Calculate top options for each city
df_top_options = cuisines_list.groupby(['city', 'cuisine_style']).agg({"rating": "mean", "reviews_number": "sum"}).sort_values(by=['city', 'cuisine_style', "reviews_number", "rating"], ascending=False)
top_options = df_top_options.groupby('city').head(50).sort_values(by=['city', "reviews_number", "rating"], ascending=[True, False, False]).round(2)

# Create base map centered on a global view
world_map = folium.Map(
    location=[20, 0],
    zoom_start=2,
    tiles="OpenStreetMap", 
    scrollWheelZoom=True,
    control_scale=True,
    width='100%',
    height='100%'
)

# Define the GeoJSON URL
geojson_url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/world-countries.json'

# Download the GeoJSON data
geo_data = requests.get(geojson_url).json()

# Define metrics with display names (in desired order)
metrics = [
    ('Cost of Living Index', 'Cost of Living Index'),
    ('GPI', 'Global Peace Index'),
    ('Rent Index', 'Rent Index'),
    ('Annual_Mean_Temperature', 'Temperature (°C)'),
    ('Groceries Index', 'Groceries Index'),
    ('Restaurant Price Index', 'Restaurant Prices'),
    ('Local Purchasing Power Index', 'Purchasing Power'),
    ('restaurants', 'Restaurant Information')
]

# Get all unique countries from all datasets and GeoJSON
all_countries = set()
for feature in geo_data['features']:
    all_countries.add(feature['properties']['name'])

# Standardize country names in the DataFrames using copy() to avoid warnings
cost_df_mapped = cost_df.copy()
gpi_latest_mapped = gpi_latest.copy()
temp_df_latest_mapped = temp_df_latest.copy()

for index, row in cost_df_mapped.iterrows():
    country = row['Country'].strip()
    if country in country_name_map:
        cost_df_mapped.at[index, 'Country_Mapped'] = country_name_map[country]
    else:
        cost_df_mapped.at[index, 'Country_Mapped'] = country

for index, row in gpi_latest_mapped.iterrows():
    country = row['Country'].strip()
    if country in country_name_map:
        gpi_latest_mapped.at[index, 'Country_Mapped'] = country_name_map[country]
    else:
        gpi_latest_mapped.at[index, 'Country_Mapped'] = country

for index, row in temp_df_latest_mapped.iterrows():
    country = row['Country'].strip()
    if country in country_name_map:
        temp_df_latest_mapped.at[index, 'Country_Mapped'] = country_name_map[country]
    else:
        temp_df_latest_mapped.at[index, 'Country_Mapped'] = country

# Create complete dataframes with all countries
complete_cost_df = cost_df_mapped.copy()
complete_gpi_df = gpi_latest_mapped.copy()
complete_temp_df = temp_df_latest_mapped.copy()

# Fill missing countries with proper null values
for country in all_countries:
    if country not in complete_cost_df['Country_Mapped'].values:
        new_row = pd.DataFrame({
            'Country_Mapped': [country], 
            'Cost of Living Index': [None], 
            'Rent Index': [None], 
            'Groceries Index': [None], 
            'Restaurant Price Index': [None], 
            'Local Purchasing Power Index': [None]
        })
        complete_cost_df = pd.concat([complete_cost_df, new_row], ignore_index=True)
    
    if country not in complete_gpi_df['Country_Mapped'].values:
        new_row = pd.DataFrame({
            'Country_Mapped': [country], 
            'GPI': [None]
        })
        complete_gpi_df = pd.concat([complete_gpi_df, new_row], ignore_index=True)
    
    if country not in complete_temp_df['Country_Mapped'].values:
        new_row = pd.DataFrame({
            'Country_Mapped': [country], 
            'Annual_Mean_Temperature': [None]
        })
        complete_temp_df = pd.concat([complete_temp_df, new_row], ignore_index=True)

# Merge datasets
merged_df = complete_cost_df.merge(complete_gpi_df, on='Country_Mapped', how='outer', suffixes=('', '_gpi'))
merged_df = merged_df.merge(complete_temp_df, on='Country_Mapped', how='outer', suffixes=('', '_temp'))

# Make sure we're using the right country name when it exists in any dataset
merged_df['Country'] = merged_df['Country'].combine_first(merged_df['Country_gpi'] if 'Country_gpi' in merged_df.columns else pd.Series([None] * len(merged_df)))
merged_df['Country'] = merged_df['Country'].combine_first(merged_df['Country_temp'] if 'Country_temp' in merged_df.columns else pd.Series([None] * len(merged_df)))

# Normalize GPI to 0-100 scale (inverted since lower GPI is better)
if 'GPI' in merged_df.columns:
    gpi_values = merged_df['GPI'].dropna()
    if len(gpi_values) > 0:
        min_gpi = gpi_values.min()
        max_gpi = gpi_values.max()
        merged_df['Normalized_GPI'] = 100 * (max_gpi - merged_df['GPI']) / (max_gpi - min_gpi)

# We don't normalize temperature as it's already in a meaningful scale (degrees Celsius)
merged_df['Normalized_Annual_Mean_Temperature'] = merged_df['Annual_Mean_Temperature']

# Normalize other metrics to 0-100 scale
for col in ['Cost of Living Index', 'Rent Index', 'Groceries Index', 'Restaurant Price Index', 'Local Purchasing Power Index']:
    if col in merged_df.columns:
        col_values = merged_df[col].dropna()
        if len(col_values) > 0:
            min_val = col_values.min()
            max_val = col_values.max()
            if max_val > min_val:  # Avoid division by zero
                merged_df[f'Normalized_{col}'] = 100 * (merged_df[col] - min_val) / (max_val - min_val)

# Create mapping dict for tooltips with normalized data
country_data = {}
for _, row in merged_df.iterrows():
    try:
        country_mapped = row['Country_Mapped'] if pd.notna(row['Country_Mapped']) else None
        if country_mapped is not None:
            data_dict = {}
            
            # Add Cost of Living data if available
            if 'Cost of Living Index' in row and pd.notna(row['Cost of Living Index']):
                data_dict['Cost of Living Index'] = float(row['Cost of Living Index'])
                if 'Normalized_Cost of Living Index' in row and pd.notna(row['Normalized_Cost of Living Index']):
                    data_dict['Normalized_Cost of Living Index'] = float(row['Normalized_Cost of Living Index'])
            
            # Add GPI data if available
            if 'GPI' in row and pd.notna(row['GPI']):
                data_dict['GPI'] = float(row['GPI'])
                if 'Normalized_GPI' in row and pd.notna(row['Normalized_GPI']):
                    data_dict['Normalized_GPI'] = float(row['Normalized_GPI'])
            
            # Add Rent data if available
            if 'Rent Index' in row and pd.notna(row['Rent Index']):
                data_dict['Rent Index'] = float(row['Rent Index'])
                if 'Normalized_Rent Index' in row and pd.notna(row['Normalized_Rent Index']):
                    data_dict['Normalized_Rent Index'] = float(row['Normalized_Rent Index'])
            
            # Add Temperature data if available
            if 'Annual_Mean_Temperature' in row and pd.notna(row['Annual_Mean_Temperature']):
                data_dict['Annual_Mean_Temperature'] = float(row['Annual_Mean_Temperature'])
                data_dict['Normalized_Annual_Mean_Temperature'] = float(row['Annual_Mean_Temperature'])
            
            # Add Groceries data if available
            if 'Groceries Index' in row and pd.notna(row['Groceries Index']):
                data_dict['Groceries Index'] = float(row['Groceries Index'])
                if 'Normalized_Groceries Index' in row and pd.notna(row['Normalized_Groceries Index']):
                    data_dict['Normalized_Groceries Index'] = float(row['Normalized_Groceries Index'])
            
            # Add Restaurant data if available
            if 'Restaurant Price Index' in row and pd.notna(row['Restaurant Price Index']):
                data_dict['Restaurant Price Index'] = float(row['Restaurant Price Index'])
                if 'Normalized_Restaurant Price Index' in row and pd.notna(row['Normalized_Restaurant Price Index']):
                    data_dict['Normalized_Restaurant Price Index'] = float(row['Normalized_Restaurant Price Index'])
            
            # Add Purchasing Power data if available
            if 'Local Purchasing Power Index' in row and pd.notna(row['Local Purchasing Power Index']):
                data_dict['Local Purchasing Power Index'] = float(row['Local Purchasing Power Index'])
                if 'Normalized_Local Purchasing Power Index' in row and pd.notna(row['Normalized_Local Purchasing Power Index']):
                    data_dict['Normalized_Local Purchasing Power Index'] = float(row['Normalized_Local Purchasing Power Index'])
            
            country_data[country_mapped] = data_dict
    except Exception as e:
        print(f"Error processing row: {e}")

# English display names for some countries that might have non-English names
english_country_names = {
    'Deutschland': 'Germany',
    'España': 'Spain',
    'Россия': 'Russia',
    'Polska': 'Poland',
    'Česko': 'Czech Republic',
    'Österreich': 'Austria',
    'Schweiz': 'Switzerland',
    'Sverige': 'Sweden',
    'Suomi': 'Finland',
    'Norge': 'Norway',
    'Danmark': 'Denmark',
    'Nederland': 'Netherlands',
    'Belgique': 'Belgium',
    'Ελλάδα': 'Greece',
    'България': 'Bulgaria',
    'România': 'Romania',
    'Magyarország': 'Hungary',
    'Slovensko': 'Slovakia',
    'Hrvatska': 'Croatia',
    'Србија': 'Serbia',
    'Ísland': 'Iceland',
    'Slovenija': 'Slovenia',
    'Latvija': 'Latvia',
    'Eesti': 'Estonia',
    'Lietuva': 'Lithuania',
    'Κύπρος': 'Cyprus',
    'Lëtzebuerg': 'Luxembourg',
    'Malta': 'Malta',
    '日本': 'Japan',
    '中国': 'China',
    '대한민국': 'South Korea',
    'भारत': 'India',
    'ประเทศไทย': 'Thailand',
    'Việt Nam': 'Vietnam',
    'Indonesia': 'Indonesia',
    'Россия': 'Russia',
    'Украина': 'Ukraine',
    'Беларусь': 'Belarus',
    'Brasil': 'Brazil',
    'México': 'Mexico',
    'Argentina': 'Argentina',
    'Chile': 'Chile',
    'Perú': 'Peru',
    'Colombia': 'Colombia',
    'Venezuela': 'Venezuela',
    'Türkiye': 'Turkey',
    'مصر': 'Egypt',
    'المغرب': 'Morocco',
    'الجزائر': 'Algeria',
    'تونس': 'Tunisia',
    'ليبيا': 'Libya',
    'السعودية': 'Saudi Arabia',
    'الإمارات': 'UAE',
    'قطر': 'Qatar',
    'الكويت': 'Kuwait',
    'عمان': 'Oman',
    'البحرين': 'Bahrain',
    'لبنان': 'Lebanon',
    'الأردن': 'Jordan',
    'سوريا': 'Syria',
    'العراق': 'Iraq',
    'إيران': 'Iran'
}

# Define city coordinates with flags
map_cities = {
    'Amsterdam': {
        'lat': 52.3547,
        'lon': 4.7638,
        'flag': 'https://i.imgur.com/blc3acB.png'
    },
    'Athens': {
        'lat': 37.9908,
        'lon': 23.7033,
        'flag': 'https://i.imgur.com/EGGLpd1.png'
    },
    'Barcelona': {
        'lat': 41.3948,
        'lon': 2.0787,
        'flag': 'https://i.imgur.com/vUh0XT5.png'
    }, 
    "Berlin": {
        'lat': 52.5069, 
        'lon': 13.3345,
        'flag': 'https://i.imgur.com/IWmwjUA.png'
    },
    "Bratislava": {
        'lat': 48.1359, 
        'lon': 16.9758,
        'flag': 'https://i.imgur.com/48ARppO.png'
    },              
    "Brussels": {
        'lat': 50.8550, 
        'lon': 4.3053,
        'flag': 'https://i.imgur.com/8dsgG0Z.png'
    },              
    "Budapest": {
        'lat': 47.4813, 
        'lon': 18.9902,
        'flag': 'https://i.imgur.com/3wn3zdO.png'
    },              
    "Copenhagen": {
        'lat': 55.6713, 
        'lon': 12.4537,
        'flag': 'https://i.imgur.com/6qIQO7a.png'
    },                
    "Dublin": {
        'lat': 53.3244, 
        'lon': -6.3857,
        'flag': 'https://i.imgur.com/XKBE096.png'
    },
    "Edinburgh": {
        'lat': 55.941, 
        'lon': -3.2753,
        'flag': 'https://i.imgur.com/D0M33Pp.png'
    },
    "Geneva": {
        'lat': 46.2050, 
        'lon': 6.1090,
        'flag': 'https://i.imgur.com/bYvB2U5.png'
    },
    "Hamburg": {
        'lat': 53.5586, 
        'lon': 9.6476,
        'flag': 'https://i.imgur.com/IWmwjUA.png'
    },
    "Helsinki": {
        'lat': 60.1100, 
        'lon': 24.7385,
        'flag': 'https://i.imgur.com/RMgJjUZ.png'
    },
    "Krakow": {
        'lat': 50.0469, 
        'lon': 19.8647,
        'flag': 'https://i.imgur.com/Pz2wDfL.png'
    },
    "Lisbon": {
        'lat': 38.7437, 
        'lon': -9.2302,
        'flag': 'https://i.imgur.com/u0PAGku.png'
    },
    "Ljubljana": {
        'lat': 46.06627, 
        'lon': 14.3920,
        'flag': 'https://i.imgur.com/SaeK70A.png'
    },
    "London": {
        'lat': 51.5287, 
        'lon': -0.3817,
        'flag': 'https://i.imgur.com/82dLnLB.png'
    },
    "Luxembourg": {
        'lat': 49.8148, 
        'lon': 5.5728,
        'flag': 'https://i.imgur.com/jKBqD0Z.png'
    },
    "Lyon": {
        'lat': 45.7580, 
        'lon': 4.7650,
        'flag': 'https://i.imgur.com/7vrY3jL.png'
    },
    "Madrid": {
        'lat': 40.4381, 
        'lon': -3.8196,
        'flag': 'https://i.imgur.com/vUh0XT5.png'
    },
    "Milan": {
        'lat': 45.4628, 
        'lon': 9.1076,
        'flag': 'https://i.imgur.com/9ciRLpM.png'
    },
    "Munich": {
        'lat': 48.1550, 
        'lon': 11.4017,
        'flag': 'https://i.imgur.com/IWmwjUA.png'
    },
    "Oporto": {
        'lat': 41.1622, 
        'lon': -8.6919,
        'flag': 'https://i.imgur.com/u0PAGku.png'
    },
    "Oslo": {
        'lat': 59.8939, 
        'lon': 10.6450,
        'flag': 'https://i.imgur.com/FM8gW1N.png'
    },
    "Paris": {
        'lat': 48.8589, 
        'lon': 2.2770,
        'flag': 'https://i.imgur.com/7vrY3jL.png'
    },
    "Prague": {
        'lat': 50.0598, 
        'lon': 14.3255,
        'flag': 'https://i.imgur.com/1gDnRgD.png'
    },
    'Rome': {
        'lat': 41.9102,
        'lon': 12.3959,
        'flag': 'https://i.imgur.com/9ciRLpM.png'
    },
    "Stockholm": {
        'lat': 59.3262, 
        'lon': 17.8419,
        'flag': 'https://i.imgur.com/VSHZpY9.png'
    },
    "Vienna": {
        'lat': 48.2208, 
        'lon': 16.2399,
        'flag': 'https://i.imgur.com/xRyqWqH.png'
    },
     "Warsaw": {
        'lat': 52.2330, 
        'lon': 20.7810,
        'flag': 'https://i.imgur.com/Pz2wDfL.png'
    },
     "Zurich": {
        'lat': 47.3775, 
        'lon': 8.4666,
        'flag': 'https://i.imgur.com/bYvB2U5.png'
    }             
}

# Default to show Cost of Living Index first
default_metric = 'Cost of Living Index'
default_title = 'Cost of Living Index'

# Create a container for the colorbar
colorbar_div = folium.Element("""
<div id="dynamic-colorbar" style="position:fixed; right:20px; bottom:20px; z-index:9999; background:white; padding:5px; border-radius:5px; box-shadow: 0 0 10px rgba(0,0,0,0.2);"></div>
""")
world_map.get_root().html.add_child(colorbar_div)

# Define different color schemes for each metric
color_schemes = {
    'Cost of Living Index': ['#ffcccc', '#ffb3b3', '#ff9999', '#ff8080', '#ff4d4d', '#cc0000'],
    'GPI': ['#e6ccb3', '#d9b38c', '#cc9966', '#bf8040', '#995c00', '#663d00'],
    'Rent Index': ['#e6ccff', '#d9b3ff', '#cc99ff', '#b366ff', '#9933ff', '#6600cc'],
    'Annual_Mean_Temperature': ['#cce6ff', '#99ccff', '#66b3ff', '#3399ff', '#0080ff', '#004d99'],
    'Groceries Index': ['#ccffcc', '#99ff99', '#66ff66', '#33cc33', '#00b300', '#006600'],
    'Restaurant Price Index': ['#ffcce6', '#ff99cc', '#ff66b3', '#ff3399', '#cc0066', '#990066'],
    'Local Purchasing Power Index': ['#ffe6cc', '#ffcc99', '#ffb366', '#ff9933', '#cc7a00', '#995c00']
}

# Define which metrics should use inverted color scales
inverted_metrics = ['Local Purchasing Power Index', 'GPI']

# Create colormaps for each metric
colormaps = {}
colorbar_htmls = {}

for col, title in metrics:
    if col != 'restaurants':  # Skip restaurants as it doesn't have a colormap
        # Use the normalized column
        norm_col = f'Normalized_{col}'
        
        # Set fixed min/max for normalized data (0-100)
        vmin = 0
        vmax = 100
        
        # Get the color scheme for this metric
        colors = color_schemes[col]
        
        # For temperature, use actual range (not normalized)
        if col == 'Annual_Mean_Temperature':
            # Use a simple linear scale for temperature with fixed endpoints
            temp_min = -10
            temp_max = 30
            
            # Create a linear colormap with fixed temperature range
            colormap = cm.LinearColormap(
                colors=colors,
                vmin=temp_min,
                vmax=temp_max,
                caption=f"{title}"
            )
        else:
            # Create fixed steps for the color scale
            steps = [0, 20, 40, 60, 80, 100]
            
            # Choose color order based on metric type
            colormap = cm.LinearColormap(
                colors=colors,
                index=steps,
                vmin=vmin,
                vmax=vmax,
                caption=f"{title}"
            )
        
        colormaps[col] = colormap
        # Store colorbar HTML for this metric
        colorbar_htmls[title] = colormap._repr_html_()

# Create a feature group for each metric
feature_groups = {}
for col, title in metrics:
    # Create a feature group
    fg = folium.FeatureGroup(name=title, show=(title == default_title))
    feature_groups[title] = fg
    
    if col == 'restaurants':
        # Add restaurant information markers at country centers
        def get_flag(city):
            flag = map_cities.get(city)
            if flag:
                flag_url = flag['flag']
                return(flag_url)
            return ""

        def get_top_options2(city):
            opt = top_options[top_options.index.get_level_values('city').isin([city])][:3]
            opt = opt.reset_index()
            opt = opt.sort_values(by=["rating", "reviews_number"], ascending=[False, False])
            top_3 = ""
            icon_class = ""
            for i in opt.iterrows():
                if (i[1]['cuisine_style'] == "Gluten Free Options") or (i[1]['cuisine_style'] == "Vegan Options"):
                    icon_class = "fa-pagelines"
                elif i[1]['cuisine_style'] == "Vegetarian Friendly":
                    icon_class = "fa-tree"
                else:
                    icon_class = "fa-globe"
                top_3 += "<div  style =\"height:25px;\"><i class=\"fa "+ icon_class + "\"></i>&nbsp;" + i[1]['cuisine_style'] + "&nbsp;" + str(i[1]['rating']) + " (" + str(i[1]['reviews_number']) +  " reviews)</div>"
            return(top_3)
        
        for k, v in map_cities.items():
            flag = get_flag(k)
            html =  "<!DOCTYPE html><html><head><link rel=\"stylesheet\" href=\"https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css\"></head><body>"
            html += "<div><div style =\"height:30px;\"><strong>{}</strong>&nbsp;<img src='{}' width='18px' height='18px'></div><div>{}</div>".format(k, flag, get_top_options2(k))
            html += "</body></html>"    
            iframe = folium.IFrame(html, width=(300)+20, height=(110)+20)
            popup = folium.Popup(iframe, max_width=1000)    
            
            folium.Marker(location =[v['lat'], v['lon']], 
                        popup=popup,
                        icon = folium.Icon(color='darkpurple', icon='fa-cutlery', prefix='fa')
            ).add_to(fg)
    else:
        # Use normalized column
        norm_col = f'Normalized_{col}'
        
        # Define a style function for this metric with strict data checking
        def style_function(feature, col=col, norm_col=norm_col, colormap=colormaps[col]):
            country_name = feature['properties']['name']
            # Only apply color if country exists in data AND has value for this metric
            if country_name in country_data:
                data = country_data[country_name]
                
                # Check for temperature (not normalized)
                if col == 'Annual_Mean_Temperature':
                    if col in data and data[col] is not None and not pd.isna(data[col]):
                        return {
                            'fillColor': colormap(data[col]),
                            'color': 'black',
                            'weight': 0.5,
                            'fillOpacity': 0.7
                        }
                
                # Check for other metrics (normalized)
                elif norm_col in data and data[norm_col] is not None and not pd.isna(data[norm_col]):
                    return {
                        'fillColor': colormap(data[norm_col]),
                        'color': 'black',
                        'weight': 0.5,
                        'fillOpacity': 0.7
                    }
            
            # No data available - use gray
            return {
                'fillColor': '#d3d3d3', 
                'color': 'black', 
                'weight': 0.5, 
                'fillOpacity': 0.5
            }

        # Create a tooltip function for this layer and metric
        def tooltip_function(feature, col=col, norm_col=norm_col, title=title):
            country_name = feature['properties']['name']
            
            # Use English name if available
            display_name = english_country_names.get(country_name, country_name)
            
            if country_name in country_data:
                data = country_data[country_name]
                
                # Build a popup with available data
                popup_content = f"""
                <div style="min-width:200px">
                    <h4 style="margin:0 0 5px;padding-bottom:5px;border-bottom:1px solid #ccc; font-weight:bold; font-size:16px;">{display_name}</h4>
                    <table style="width:100%;border-collapse:collapse;font-size:13px; margin-top:5px;">
                """
                
                # Show whether current metric is available
                metric_available = False
                current_value = None
                
                if col == 'Annual_Mean_Temperature':
                    if col in data and pd.notna(data[col]):
                        metric_available = True
                        current_value = data[col]
                else:
                    if col in data and pd.notna(data[col]):
                        metric_available = True
                        current_value = data[col]
                
                # Add available metrics to popup
                if 'Cost of Living Index' in data and pd.notna(data['Cost of Living Index']):
                    popup_content += f"<tr><td><b>Cost of Living:</b></td><td align='right'>{data['Cost of Living Index']:.1f}</td></tr>"
                
                if 'GPI' in data and pd.notna(data['GPI']):
                    popup_content += f"<tr><td><b>Peace Index:</b></td><td align='right'>{data['GPI']:.3f}</td></tr>"
                
                if 'Rent Index' in data and pd.notna(data['Rent Index']):
                    popup_content += f"<tr><td><b>Rent:</b></td><td align='right'>{data['Rent Index']:.1f}</td></tr>"
                
                if 'Annual_Mean_Temperature' in data and pd.notna(data['Annual_Mean_Temperature']):
                    popup_content += f"<tr><td><b>Temperature:</b></td><td align='right'>{data['Annual_Mean_Temperature']:.1f}°C</td></tr>"
                
                if 'Groceries Index' in data and pd.notna(data['Groceries Index']):
                    popup_content += f"<tr><td><b>Groceries:</b></td><td align='right'>{data['Groceries Index']:.1f}</td></tr>"
                
                if 'Restaurant Price Index' in data and pd.notna(data['Restaurant Price Index']):
                    popup_content += f"<tr><td><b>Restaurant:</b></td><td align='right'>{data['Restaurant Price Index']:.1f}</td></tr>"
                
                if 'Local Purchasing Power Index' in data and pd.notna(data['Local Purchasing Power Index']):
                    popup_content += f"<tr><td><b>Purchasing Power:</b></td><td align='right'>{data['Local Purchasing Power Index']:.1f}</td></tr>"
                
                # Warn if current metric is not available
                if not metric_available:
                    popup_content += f"""
                        <tr><td colspan='2' style='color:red; font-weight:bold; padding-top:10px;'>
                            Current metric ({title}) not available
                        </td></tr>
                    """
                
                popup_content += """
                    </table>
                    <div style="margin-top:8px;font-weight:bold;color:#c00; font-size:14px;">
                        Current View: """ + title
                
                if metric_available and current_value is not None:
                    if col == 'Annual_Mean_Temperature':
                        popup_content += f" ({current_value:.1f}°C)"
                    elif col == 'GPI':
                        popup_content += f" ({current_value:.3f})"
                    else:
                        popup_content += f" ({current_value:.1f})"
                else:
                    popup_content += " (No data)"
                
                popup_content += """
                    </div>
                </div>
                """
                
                return popup_content
            else:
                return f"<b>{display_name}</b><br>No data available"

        # Add the GeoJSON layer with styling for this metric
        geo_json = folium.GeoJson(
            geo_data,
            name=title,
            style_function=style_function,
            highlight_function=lambda x: {'weight': 2, 'color': '#333333', 'fillOpacity': 0.8}
        )
        
        # Add the GeoJSON layer to the feature group
        geo_json.add_to(fg)
        
        # Add country labels and tooltips with improved geometric placement
        for feature in geo_data['features']:
            country_name = feature['properties']['name']
            display_name = english_country_names.get(country_name, country_name)
            
            if country_name in country_data:
                try:
                    # Convert the geometry to a shapely object
                    country_geom = shape(feature['geometry'])
                    
                    # Handle MultiPolygon (countries with multiple parts like islands)
                    if country_geom.geom_type == 'MultiPolygon':
                        # Find the largest polygon in the MultiPolygon
                        largest_polygon = max(country_geom.geoms, key=lambda a: a.area)
                        # Use representative_point which guarantees the point is within the polygon
                        label_point = largest_polygon.representative_point()
                    else:
                        # For simple polygons, just use representative_point
                        label_point = country_geom.representative_point()
                    
                    # Get the coordinates from the point
                    center = (label_point.y, label_point.x)  # Folium uses (lat, lon)
                    
                    # Only add labels for countries with area above threshold (to avoid cluttering)
                    if country_geom.area > 0.5:  # Threshold can be adjusted
                        # Create a hover tooltip for this country
                        tooltip_html = tooltip_function(feature)
                        
                        # Create a div icon with class for JavaScript to control
                        icon = folium.DivIcon(
                            icon_size=(100, 20),
                            icon_anchor=(50, 10),
                            html=f'''
                                <div class="country-label" 
                                     data-country="{country_name}" 
                                     data-area="{country_geom.area:.2f}" 
                                     style="font-size: 10px; 
                                            color: #333; 
                                            font-weight: bold; 
                                            text-shadow: 1px 1px 1px #fff, -1px -1px 1px #fff, 1px -1px 1px #fff, -1px 1px 1px #fff; 
                                            text-align: center;">
                                    {display_name}
                                </div>
                            '''
                        )
                        
                        # Add the label marker
                        marker = folium.Marker(
                            location=center,
                            icon=icon,
                            tooltip=folium.Tooltip(tooltip_html, sticky=True)
                        )
                        marker.add_to(fg)
                except Exception as e:
                    # Skip countries where geometry calculations fail
                    print(f"Error processing {country_name}: {e}")
                    continue
    
    # Add this feature group to the map
    fg.add_to(world_map)

# Add layer control to toggle between metrics
folium.LayerControl(collapsed=False).add_to(world_map)

# Create a dynamic title header for the map
header_html = """
<div id="dynamic-title" style="position:fixed; top:10px; left:50%; transform:translateX(-50%); 
    z-index:9999; background:white; padding:5px 10px; border-radius:5px; 
    font-family:Arial; font-weight:bold; font-size:16px; 
    box-shadow: 0 0 10px rgba(0,0,0,0.2);">
    Global Indicators Map - <span id="metric-title">Cost of Living Index</span>
</div>
"""
world_map.get_root().html.add_child(folium.Element(header_html))

# Add JavaScript to handle layer switching, dynamic colorbar, and dynamic title
js_code = """
<script>
(function() {
    // Store all colorbar HTMLs
    var colorbarHTMLs = {
"""

# Add each metric's colorbar HTML as a JavaScript string
for i, (col, title) in enumerate(metrics):
    if col != 'restaurants':  # Skip restaurants since it doesn't have a colorbar
        if i > 0:
            js_code += ",\n"
        # Properly escape the HTML for JavaScript
        html_escaped = colorbar_htmls[title].replace('\\', '\\\\').replace("'", "\\'").replace('\n', '\\n')
        js_code += f"        '{title}': '{html_escaped}'"

js_code += """
    };
    
    // Function to update the colorbar and title
    function updateColorbarAndTitle(layerName) {
        var colorbarDiv = document.getElementById('dynamic-colorbar');
        var titleSpan = document.getElementById('metric-title');
        
        if (layerName === 'Restaurant Information') {
            // Hide colorbar for restaurants
            colorbarDiv.innerHTML = '';
        } else if (colorbarHTMLs[layerName]) {
            colorbarDiv.innerHTML = colorbarHTMLs[layerName];
        }
        
        if (titleSpan) {
            titleSpan.textContent = layerName;
        }
    }
    
    // Function to handle responsive country labels
    function updateCountryLabels(zoomLevel) {
        var labels = document.querySelectorAll('.country-label');
        
        labels.forEach(function(label) {
            var countryArea = parseFloat(label.getAttribute('data-area') || '0');
            
            // Scale font size based on zoom level and country area
            var baseFontSize = 10;
            var scaleFactor = Math.min(zoomLevel / 2, 2.5);
            
            // Adjust font size based on country size and zoom level
            if (zoomLevel < 3) {
                // At lower zoom levels, only show larger countries
                if (countryArea < 5) {
                    label.style.display = 'none';
                } else {
                    label.style.display = 'block';
                    var fontSize = Math.max(baseFontSize * scaleFactor * 0.8, 8);
                    label.style.fontSize = fontSize + 'px';
                }
            } else if (zoomLevel < 5) {
                // At medium zoom levels, show medium and larger countries
                if (countryArea < 1) {
                    label.style.display = 'none';
                } else {
                    label.style.display = 'block';
                    var fontSize = Math.max(baseFontSize * scaleFactor * 0.9, 9);
                    label.style.fontSize = fontSize + 'px';
                }
            } else {
                // At higher zoom levels, show all countries
                label.style.display = 'block';
                var fontSize = Math.max(baseFontSize * scaleFactor, 10);
                label.style.fontSize = fontSize + 'px';
            }
            
            // Make labels more visible at higher zoom levels
            var opacity = Math.min(1, 0.7 + (zoomLevel - 2) * 0.1);
            label.style.opacity = opacity.toString();
        });
    }
    
    // Function to completely remove all map features
    function removeAllFeatures() {
        var map = document.querySelector('.folium-map')._leaflet_map;
        if (map) {
            var layersToRemove = [];
            
            // Collect all layers that need to be removed
            map.eachLayer(function(layer) {
                // Keep only the base tile layer
                if (!layer._url) {
                    layersToRemove.push(layer);
                }
            });
            
            // Remove all collected layers
            layersToRemove.forEach(function(layer) {
                map.removeLayer(layer);
            });
            
            // Remove any lingering markers or labels
            var markerElements = document.querySelectorAll('.leaflet-marker-pane');
            markerElements.forEach(function(element) {
                while (element.firstChild) {
                    element.removeChild(element.firstChild);
                }
            });
            
            // Clear tooltip pane
            var tooltipElements = document.querySelectorAll('.leaflet-tooltip-pane');
            tooltipElements.forEach(function(element) {
                while (element.firstChild) {
                    element.removeChild(element.firstChild);
                }
            });
        }
    }
    
    // Function to force layer recreation
    function forceLayerReload(metricName) {
        // Save current map view
        var map = document.querySelector('.folium-map')._leaflet_map;
        var center = map.getCenter();
        var zoom = map.getZoom();
        
        // First, completely remove all features
        removeAllFeatures();
        
        // Wait for removal to complete
        setTimeout(function() {
            // Uncheck all checkboxes
            var layerControls = document.querySelectorAll('.leaflet-control-layers-overlays input[type="checkbox"]');
            layerControls.forEach(function(checkbox) {
                checkbox.checked = false;
            });
            
            // Wait a bit more
            setTimeout(function() {
                // Click the correct checkbox to recreate the layer
                layerControls.forEach(function(checkbox) {
                    var labelText = checkbox.nextElementSibling.textContent.trim();
                    if (labelText === metricName) {
                        checkbox.checked = true;
                        // Trigger the change event manually
                        var event = new Event('change', { bubbles: true });
                        checkbox.dispatchEvent(event);
                    }
                });
                
                // Restore map view
                setTimeout(function() {
                    map.setView(center, zoom);
                }, 300);
            }, 150);
        }, 100);
    }
    
    // Set default colorbar and title
    setTimeout(function() {
        // Set the initial colorbar
        updateColorbarAndTitle('""" + default_title + """');
        
        // Get map instance
        var map = document.querySelector('.folium-map')._leaflet_map;
        if (map) {
            // Initial update of label sizes
            updateCountryLabels(map.getZoom());
            
            // Listen for zoom changes
            map.on('zoomend', function() {
                updateCountryLabels(map.getZoom());
            });
        }
        
        // Add event listeners to layer control checkboxes after they're fully loaded
        var checkInterval = setInterval(function() {
            var layerControls = document.querySelectorAll('.leaflet-control-layers-overlays input[type="checkbox"]');
            if (layerControls.length > 0) {
                clearInterval(checkInterval);
                
                layerControls.forEach(function(checkbox) {
                    checkbox.addEventListener('change', function() {
                        if (this.checked) {
                            // Get the layer name from the next element (the label)
                            var layerName = this.nextElementSibling.textContent.trim();
                            
                            // Uncheck all other checkboxes immediately
                            layerControls.forEach(function(cb) {
                                if (cb !== checkbox && cb.checked) {
                                    cb.checked = false;
                                }
                            });
                            
                            // Update colorbar and title
                            updateColorbarAndTitle(layerName);
                            
                            // Force complete reload with slight delay
                            setTimeout(function() {
                                forceLayerReload(layerName);
                            }, 50);
                        }
                    });
                });
            }
        }, 200);
    }, 1000);
})();
</script>
"""

world_map.get_root().html.add_child(folium.Element(js_code))

# Add CSS to make the map fill the container
css = """
<style>
.folium-map {
    width: 100%;
    height: 100vh;
    position: absolute;
    top: 0;
    left: 0;
}
.country-label {
    white-space: nowrap;
    pointer-events: none;
    text-align: center;
    transition: font-size 0.2s ease;
}
.leaflet-tooltip {
    font-family: Arial, sans-serif;
}
/* Better contrast for country labels */
.country-label {
    text-shadow: 
        -1px -1px 0 #fff,
        1px -1px 0 #fff,
        -1px 1px 0 #fff,
        1px 1px 0 #fff,
        0 -2px 0 #fff,
        0 2px 0 #fff,
        -2px 0 0 #fff,
        2px 0 0 #fff;
    font-weight: bold;
}
</style>
"""

world_map.get_root().html.add_child(folium.Element(css))

# Save the map as an HTML file
world_map.save('global_cost_of_living_map.html')

# Display the map
world_map
